# EDA: financial_loan.csv

Цель — понять распределения признаков, категории, временные паттерны и контекст (праздники/ковид/макро‑события)

In [30]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go

px.defaults.template = 'plotly_white'
px.defaults.width = 900
px.defaults.height = 380

pd.set_option('display.max_columns', 200)
pd.set_option('display.width', 140)

In [31]:
df = pd.read_csv('financial_loan.csv')
for c in ['issue_date','last_credit_pull_date','last_payment_date','next_payment_date']:
    df[c] = pd.to_datetime(df[c], dayfirst=True, errors='coerce')
print(df.shape)
df.head()

(38576, 24)


id address_state application_type emp_length              emp_title grade home_ownership issue_date last_credit_pull_date  \
0  1077430            GA       INDIVIDUAL   < 1 year                  Ryder     C           RENT 2021-02-11            2021-09-13   
1  1072053            CA       INDIVIDUAL    9 years         MKC Accounting     E           RENT 2021-01-01            2021-12-14   
2  1069243            CA       INDIVIDUAL    4 years  Chemat Technology Inc     C           RENT 2021-01-05            2021-12-12   
3  1041756            TX       INDIVIDUAL   < 1 year    barnes distribution     B       MORTGAGE 2021-02-25            2021-12-12   
4  1068350            IL       INDIVIDUAL  10+ years          J&J Steel Inc     A       MORTGAGE 2021-01-01            2021-12-14   

  last_payment_date  loan_status next_payment_date  member_id purpose sub_grade        term verification_status  annual_income     dti  \
0        2021-04-13  Charged Off        2021-05-13    1314167     car        C4   60 months     Source Verified        30000.0  0.0100   
1        2021-01-15   Fully Paid        2021-02-15    1288686     car        E1   36 months     Source Verified        48000.0  0.0535   
2        2021-01-09  Charged Off        2021-02-09    1304116     car        C5   36 months        Not Verified        50000.0  0.2088   
3        2021-03-12   Fully Paid        2021-04-12    1272024     car        B2   60 months     Source Verified        42000.0  0.0540   
4        2021-01-15   Fully Paid        2021-02-15    1302971     car        A1   36 months            Verified        83000.0  0.0231   

   installment  int_rate  loan_amount  total_acc  total_payment  
0        59.83    0.1527         2500          4           1009  
1       109.43    0.1864         3000          4           3939  
2       421.65    0.1596        12000         11           3522  
3        97.06    0.1065         4500          9           4911  
4       106.53    0.0603         3500         28           3835

## Общий обзор

In [32]:
df.info()

print('duplicates:', df.duplicated().sum())

df.describe().T

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 38576 entries, 0 to 38575
Data columns (total 24 columns):
 #   Column                 Non-Null Count  Dtype         
---  ------                 --------------  -----         
 0   id                     38576 non-null  int64         
 1   address_state          38576 non-null  object        
 2   application_type       38576 non-null  object        
 3   emp_length             38576 non-null  object        
 4   emp_title              37138 non-null  object        
 5   grade                  38576 non-null  object        
 6   home_ownership         38576 non-null  object        
 7   issue_date             38576 non-null  datetime64[ns]
 8   last_credit_pull_date  38576 non-null  datetime64[ns]
 9   last_payment_date      38576 non-null  datetime64[ns]
 10  loan_status            38576 non-null  object        
 11  next_payment_date      38576 non-null  datetime64[ns]
 12  member_id              38576 non-null  int64         
 13  p

count                           mean                  min                  25%                  50%  \
id                     38576.0                  681037.061385              54734.0             513517.0             662728.0   
issue_date               38576  2021-07-16 02:31:35.562007040  2021-01-01 00:00:00  2021-04-11 00:00:00  2021-07-11 00:00:00   
last_credit_pull_date    38576  2021-06-08 13:36:34.193280512  2021-01-08 00:00:00  2021-04-15 00:00:00  2021-05-16 00:00:00   
last_payment_date        38576  2021-06-26 09:52:08.909166080  2021-01-08 00:00:00  2021-03-16 00:00:00  2021-06-14 00:00:00   
next_payment_date        38576  2021-07-26 20:42:20.605557760  2021-02-08 00:00:00  2021-04-16 00:00:00  2021-07-14 00:00:00   
member_id              38576.0                  847651.506299              70699.0            662978.75             847356.5   
annual_income          38576.0                    69644.54031               4000.0              41500.0              60000.0   
dti                    38576.0                       0.133274                  0.0               0.0821               0.1342   
installment            38576.0                     326.862965                15.69               168.45              283.045   
int_rate               38576.0                       0.120488               0.0542               0.0932               0.1186   
loan_amount            38576.0                   11296.066855                500.0               5500.0              10000.0   
total_acc              38576.0                      22.132544                  2.0                 14.0                 20.0   
total_payment          38576.0                   12263.348533                 34.0               5633.0              10042.0   

                                       75%                  max            std  
id                                836506.0            1077501.0  211324.578218  
issue_date             2021-10-11 00:00:00  2021-12-12 00:00:00            NaN  
last_credit_pull_date  2021-08-13 00:00:00  2022-01-20 00:00:00            NaN  
last_payment_date      2021-09-15 00:00:00  2021-12-15 00:00:00            NaN  
next_payment_date      2021-10-15 00:00:00  2022-01-15 00:00:00            NaN  
member_id                        1045652.5            1314167.0   266810.45686  
annual_income                      83200.5            6000000.0   64293.681045  
dti                                 0.1859               0.2999       0.066662  
installment                       434.4425              1305.19        209.092  
int_rate                            0.1459               0.2459       0.037164  
loan_amount                        15000.0              35000.0    7460.746022  
total_acc                             29.0                 90.0      11.392282  
total_payment                      16658.0              58564.0    9051.104777

Вывод: базовый объём — 38,576 строк и 24 колонки, дубликатов строк нет.

## Пропуски

In [33]:
summary = pd.DataFrame({
    'dtype': df.dtypes.astype(str),
    'missing': df.isna().sum(),
    'missing_%': (df.isna().mean() * 100).round(2),
    'unique': df.nunique(),
    'example': df.head(1).T[0]
}).sort_values('missing_%', ascending=False)
summary

dtype  missing  missing_%  unique              example
emp_title                      object     1438       3.73   28525                Ryder
id                              int64        0       0.00   38576              1077430
purpose                        object        0       0.00      14                  car
total_acc                       int64        0       0.00      82                    4
loan_amount                     int64        0       0.00     880                 2500
int_rate                      float64        0       0.00     371               0.1527
installment                   float64        0       0.00   15132                59.83
dti                           float64        0       0.00    2863                 0.01
annual_income                 float64        0       0.00    5096              30000.0
verification_status            object        0       0.00       3      Source Verified
term                           object        0       0.00       2            60 months
sub_grade                      object        0       0.00      35                   C4
member_id                       int64        0       0.00   38576              1314167
address_state                  object        0       0.00      50                   GA
next_payment_date      datetime64[ns]        0       0.00     102  2021-05-13 00:00:00
loan_status                    object        0       0.00       3          Charged Off
last_payment_date      datetime64[ns]        0       0.00     102  2021-04-13 00:00:00
last_credit_pull_date  datetime64[ns]        0       0.00     107  2021-09-13 00:00:00
issue_date             datetime64[ns]        0       0.00      65  2021-02-11 00:00:00
home_ownership                 object        0       0.00       5                 RENT
grade                          object        0       0.00       7                    C
emp_length                     object        0       0.00      11             < 1 year
application_type               object        0       0.00       1           INDIVIDUAL
total_payment                   int64        0       0.00   19525                 1009

Вывод: существенные пропуски есть только в `emp_title` (~1438 строк), остальные признаки полные.

## Страна и география

In [34]:
state_vals = set(df['address_state'].dropna().unique().tolist())
print('unique address_state:', len(state_vals))
print('sample:', sorted(list(state_vals))[:10])

unique address_state: 50
sample: ['AK', 'AL', 'AR', 'AZ', 'CA', 'CO', 'CT', 'DC', 'DE', 'FL']


Вывод: Все значения address_state совпадают с двухбуквенными кодами штатов США. США - страна данных.

## Категориальные признаки: распределения

In [35]:
# address_state
vc = df['address_state'].value_counts()
fig = px.bar(vc.sort_values(), orientation='h', labels={'value':'count','index':'address_state'})
fig.update_layout(title='address_state')
fig.show()

Вывод: `address_state` — категорий: **50**,Самые частые: CA, NY, FL

In [36]:
# emp_length
vc = df['emp_length'].value_counts()
fig = px.bar(vc.sort_values(), orientation='h', labels={'value':'count','index':'emp_length'})
fig.update_layout(title='emp_length')
fig.show()

Вывод: `emp_length` — категорий: **11**,Самые частые: 10+ years, < 1 year, 2 years.

In [37]:
# emp_title (группировка редких значений)
vc = df['emp_title'].fillna('MISSING').value_counts()
N = 25

keep = vc.head(N)
other = vc.iloc[N:].sum()
vc_grouped = pd.concat([keep, pd.Series({'Other': other})])

fig = px.bar(vc_grouped.sort_values(), orientation='h', labels={'value':'count','index':'emp_title'})
fig.update_layout(title='emp_title: top-25 + Other')
fig.show()

In [39]:
import re

def norm_emp_title(x):
    if x is None or (isinstance(x, float) and pd.isna(x)):
        return "missing"
    x = str(x).lower()
    x = re.sub(r"[^\w]", "", x)
    x = re.sub(r"\s+", "", x)
    return x if x != "" else "missing"

work = df.copy()
work["emp_title_norm"] = work["emp_title"].apply(norm_emp_title)

counts = work[work["emp_title_norm"] != "missing"]["emp_title_norm"].value_counts()

display(counts.head(10))
len(counts)

emp_title_norm
usarmy              264
bankofamerica       139
walmart             116
jpmorganchase        96
selfemployed         96
att                  95
uspostalservice      77
wellsfargo           73
usairforce           73
kaiserpermanente     69
Name: count, dtype: int64

26355

Вывод: `emp_title` — **очень высокая кардинальность** (категорий: 28526). Имеет смысл поработать с классификацией и посомотреть группировку emp_title по штатам. Имеет смысл сгруппировать по виду деятельности. Проведена нормализация и канонизация топовых сущностей, количество категорий снизилось несильно 28526. Из предложений можно построить расстояние левенштейна. Интересное значение Target - может быть это разметка на мошенника?

In [86]:
# grade
vc = df['grade'].value_counts()
fig = px.bar(vc.sort_values(), orientation='h', labels={'value':'count','index':'grade'})
fig.update_layout(title='grade')
fig.show()


Вывод: `grade` — категорий: **7**, Самые частые: B, A, C.

In [87]:
# home_ownership
vc = df['home_ownership'].value_counts()
fig = px.bar(vc.sort_values(), orientation='h', labels={'value':'count','index':'home_ownership'})
fig.update_layout(title='home_ownership')
fig.show()

Вывод: `home_ownership` — категорий: **5**. Самые частые: RENT (в аренде), MORTGAGE (ипотека), OWN (собственнность). Есть странные категории, видимо, бездомные

In [88]:
# loan_status
vc = df['loan_status'].value_counts()
fig = px.bar(vc.sort_values(), orientation='h', labels={'value':'count','index':'loan_status'})
fig.update_layout(title='loan_status')
fig.show()


Вывод: `loan_status` — категорий: **3**. Это статус дефолта кредита.

In [89]:
# purpose
vc = df['purpose'].value_counts()
fig = px.bar(vc.sort_values(), orientation='h', labels={'value':'count','index':'purpose'})
fig.update_layout(title='purpose')
fig.show()


Вывод: `purpose` — категорий: **14**. Самые частые: Debt consolidation (рефинансирование), credit card, other (что бы это не значило).

In [90]:
# sub_grade
vc = df['sub_grade'].value_counts()
fig = px.bar(vc.sort_values(), orientation='h', labels={'value':'count','index':'sub_grade'})
fig.update_layout(title='sub_grade')
fig.show()

Вывод: `sub_grade` — категорий: **35**,Самые частые: B3, A4, A5. Не самая понятная категория

In [91]:
# term
vc = df['term'].value_counts()
fig = px.bar(vc.sort_values(), orientation='h', labels={'value':'count','index':'term'})
fig.update_layout(title='term')
fig.show()

Вывод: `term` — категорий: **2**. Выдавали только на 3 или 5 лет кредиты

In [93]:
# verification_status
vc = df['verification_status'].value_counts()
fig = px.bar(vc.sort_values(), orientation='h', labels={'value':'count','index':'verification_status'})
fig.update_layout(title='verification_status')
fig.show()

Вывод: `verification_status` — категорий: **3**. Чаще всего кредиты выдавали с неподтвержденным источником дохода, Source verified - проверен через внешний источник

## Числовые признаки: распределения

In [94]:
# annual_income
fig = px.histogram(df, x='annual_income', nbins=40, title='annual_income: histogram')
fig.update_xaxes(title='annual_income')
fig.update_yaxes(title='count')
fig.show()

fig2 = px.box(df, x='annual_income', title='annual_income: boxplot')
fig2.update_xaxes(title='annual_income')
fig2.show()

Вывод: `annual_income` — медиана 60000.00, p95 144000.00, min 4000.00, max 6000000.00. Распределение правостороннее (длинный хвост).

In [95]:
# dti
fig = px.histogram(df, x='dti', nbins=40, title='dti: histogram')
fig.update_xaxes(title='dti')
fig.update_yaxes(title='count')
fig.show()

fig2 = px.box(df, x='dti', title='dti: boxplot')
fig2.update_xaxes(title='dti')
fig2.show()

Вывод: `dti` — медиана 0.13, p95 0.24, min 0.00, max 0.30. Распределение умеренно асимметричное. Это ежемесячный долг / ежемесячный доход

In [97]:
# installment
fig = px.histogram(df, x='installment', nbins=40, title='installment: histogram')
fig.update_xaxes(title='installment')
fig.update_yaxes(title='count')
fig.show()

fig2 = px.box(df, x='installment', title='installment: boxplot')
fig2.update_xaxes(title='installment')
fig2.show()


Вывод: `installment` — медиана 283.05, p95 767.67, min 15.69, max 1305.19. Распределение правостороннее (длинный хвост). Это размер ежемесячнго платежа по кредиту

In [98]:
# int_rate
fig = px.histogram(df, x='int_rate', nbins=40, title='int_rate: histogram')
fig.update_xaxes(title='int_rate')
fig.update_yaxes(title='count')
fig.show()

fig2 = px.box(df, x='int_rate', title='int_rate: boxplot')
fig2.update_xaxes(title='int_rate')
fig2.show()

Вывод: `int_rate` — медиана 0.12, p95 0.19, min 0.05, max 0.25. Распределение умеренно правосторонне асимметричное, большиснтво нормальном диапазоне, но есть правый хвост.  Это ставка по кредиту.

In [99]:
# loan_amount
fig = px.histogram(df, x='loan_amount', nbins=40, title='loan_amount: histogram')
fig.update_xaxes(title='loan_amount')
fig.update_yaxes(title='count')
fig.show()

fig2 = px.box(df, x='loan_amount', title='loan_amount: boxplot')
fig2.update_xaxes(title='loan_amount')
fig2.show()

Вывод: `loan_amount` — медиана 10000.00, p95 25000.00, min 500.00, max 35000.00. Распределение правостороннее (длинный хвост). Это сумма залога.

In [100]:
# total_acc
fig = px.histogram(df, x='total_acc', nbins=40, title='total_acc: histogram')
fig.update_xaxes(title='total_acc')
fig.update_yaxes(title='count')
fig.show()

fig2 = px.box(df, x='total_acc', title='total_acc: boxplot')
fig2.update_xaxes(title='total_acc')
fig2.show()

Вывод: `total_acc` — медиана 20.00, p95 43.00, min 2.00, max 90.00. Это показатель кредитных аккаунтов, то есть кридитной истории.

In [101]:
# total_payment
fig = px.histogram(df, x='total_payment', nbins=40, title='total_payment: histogram')
fig.update_xaxes(title='total_payment')
fig.update_yaxes(title='count')
fig.show()

fig2 = px.box(df, x='total_payment', title='total_payment: boxplot')
fig2.update_xaxes(title='total_payment')
fig2.show()

Вывод: `total_payment` — медиана 10042.00, p95 30320.25, min 34.00, max 58564.00. Распределение правостороннее (длинный хвост). Постфактум историческая величина, которая показывает текущее обслуживание кредита. потенцаильный лик. Показывает сумму выплаты.

## Даты и календарный контекст

In [104]:
#issue_date
issue_counts = df['issue_date'].value_counts().sort_index()

fig = px.bar(issue_counts, labels={'index':'date','value':'count'}, title='issue_date: количество записей по датам')
fig.update_xaxes(title='date')
fig.update_yaxes(title='count')
fig.show()

In [108]:
# аутлайрс все даты, которые НЕ попадают в 7-11
out = df[~df['issue_date'].dt.day.between(7, 11)]
out_dates = out['issue_date'].value_counts().sort_index()
display(out_dates)

issue_date
2021-01-01    2
2021-01-05    1
2021-02-02    1
2021-02-25    1
2021-07-17    1
2021-07-22    1
2021-09-02    1
2021-11-19    1
2021-12-02    1
2021-12-12    1
Name: count, dtype: int64

Вывод: `issue_date` имеет 65 (Вне этого окна найдено 11 одиночных записей — вероятные догрузки/аномалии; на анализ не влияют, поэтому удалены/помечены флагом) уникальных дат, диапазон 2021-01-01 — 2021-12-12. Интересно, что это повторяющиеся периоды с 8-11 числа каждого месяца в основном (есть аномалии). А с июля так еще и с 7 по 11 числа. Термин issue_date обычно означает дату выпуска/выдачи, однако в данном датасете распределение issue_date указывает, что это скорее дата среза/выгрузки данных, а не дата выдачи кредита.

## Даты: разницы между событиями

In [110]:
work = df.copy()
work['days_last_payment_minus_issue'] = (work['last_payment_date'] - work['issue_date']).dt.days
work['days_last_credit_pull_minus_issue'] = (work['last_credit_pull_date'] - work['issue_date']).dt.days
work['days_next_payment_minus_last'] = (work['next_payment_date'] - work['last_payment_date']).dt.days
work['days_next_payment_minus_issue'] = (work['next_payment_date'] - work['issue_date']).dt.days
for c in ['days_last_payment_minus_issue','days_last_credit_pull_minus_issue','days_next_payment_minus_last', "days_next_payment_minus_issue"]:
    fig = px.histogram(work, x=c, nbins=60, title=c)
    fig.update_xaxes(title='days')
    fig.update_yaxes(title='count')
    fig.show()

work[['days_last_payment_minus_issue','days_last_credit_pull_minus_issue','days_next_payment_minus_last', "days_next_payment_minus_issue"]].describe().T.val

count       mean         std    min    25%   50%   75%    max
days_last_payment_minus_issue      38576.0 -19.694058  127.222933 -336.0  -90.0   3.0  34.0  338.0
days_last_credit_pull_minus_issue  38576.0 -37.538210  128.213332 -333.0 -146.0 -26.0  34.0  347.0
days_next_payment_minus_last       38576.0  30.451524    0.857121   28.0   30.0  31.0  31.0   31.0
days_next_payment_minus_issue      38576.0  10.757466  127.340816 -305.0  -60.0  34.0  64.0  369.0

Вывод: лаги дат имеют как положительные, так и отрицательные значения; это подтверждает, что `issue_date` — дата среза/выгрузки, а не дата выдачи кредита.

### Словарь колонок
| Колонка | Что означает |
|---|---|
| id | Идентификатор (тех. ключ). |
| address_state | Штат проживания заемщика (США). |
| application_type | Тип заявки (индивидуальная). |
| emp_length | Стаж занятости заемщика. |
| emp_title | Должность/профессия заемщика. В свободной форме. |
| grade | Класс кредита (агрегированный риск‑скоринг). |
| home_ownership | Статус владения жильём. |
| issue_date | Дата выгрузки/среза записи. |
| last_credit_pull_date | Дата последней проверки кредитной истории. |
| last_payment_date | Дата последнего платежа по кредиту. |
| loan_status | Статус кредита (Fully Paid/Charged Off/Current). |
| next_payment_date | Плановая дата следующего платежа. |
| member_id | Идентификатор (тех. ключ). |
| purpose | Цель кредита. |
| sub_grade | Подкласс риска (детализация grade). |
| term | Срок кредита (в месяцах). |
| verification_status | Статус проверки дохода. |
| annual_income | Годовой доход заемщика. |
| dti | Debt‑to‑income: долговая нагрузка к доходу. |
| installment | Ежемесячный платеж. |
| int_rate | Процентная ставка по кредиту. |
| loan_amount | Сумма кредита. |
| total_acc | Количество кредитных линий. |
| total_payment | Суммарно выплачено по займу. |